In [1]:
#修改起始id,出处,文件名
starting_id = 12655
origin = "2023届宝山区一模"
filename = r"C:\Users\weiye\Documents\wwy sync\临时工作区\自拟题目3.tex"
editor = "20221217\t王伟叶"

In [10]:
import os,re,json

#从enumerate环境的字符串生成题目列表
def GenerateProblemListFromString(data):
    try:
        data = re.findall(r"\\begin\{document\}([\s\S]*?)\\end\{document\}",data)[0]
    except:
        pass
    data = re.sub(r"\n[\s]*?\%[\s\S]*?\n","\n",data)
    data = re.sub(r"\n{2,}","\n",data)
    data = re.sub(r"\\item",r"\\enditem\\item",data)
    data = re.sub(r"\\end\{enumerate\}",r"\\enditem",data)
    ProblemList = [p.strip() for p in re.findall(r"\\item([\s\S]*?)\\enditem",data)]
    return ProblemList

# 创建新的空题目
def CreateEmptyProblem(problem):
    NewProblem = problem.copy()
    for field in NewProblem:
        if type(NewProblem[field]) == str:
            NewProblem[field] = ""
        elif type(NewProblem[field]) == list:
            NewProblem[field] = []
        elif type(NewProblem[field]) == int or type(NewProblem[field]) == float:
            NewProblem[field] = -1
    return NewProblem

# 创建新题目
def CreateNewProblem(id,content,origin,dict,editor):
    NewProblem = CreateEmptyProblem(dict["000001"])
    NewProblem["id"] = str(id).zfill(6)
    NewProblem["content"] = content
    NewProblem["origin"] = origin
    NewProblem["edit"] = [editor]
    return NewProblem

duplicate_flag = False

with open(r"../题库0.3/Problems.json","r",encoding = "utf8") as f:
    database = f.read()
pro_dict = json.loads(database)

with open(filename,"r",encoding = "utf8") as f:
    problems_string = f.read()
problems = GenerateProblemListFromString(problems_string)

id = starting_id
for p in problems:
    pid = str(id).zfill(6)
    if pid in pro_dict:
        duplicate_flag = True
    # NewProblem = CreateNewProblem(id = pid, content = p, origin = origin , dict = pro_dict,editor = editor)
    NewProblem = CreateNewProblem(id = pid, content = p, origin = origin + "试题" + str(id- starting_id+1), dict = pro_dict,editor = editor)
    pro_dict[pid] = NewProblem
    id += 1

#按id排序生成字典
sorted_dict_id = sorted(pro_dict)
sorted_dict = {}
for id in sorted_dict_id:
    sorted_dict[id] = pro_dict[id]
#将排序后的字典转为json

if not duplicate_flag:
    new_database = json.dumps(sorted_dict,indent = 4,ensure_ascii=False)
    #写入json数据库文件
    with open(r"../题库0.3/Problems.json","w",encoding = "utf8") as f:
        f.write(new_database)
else:
    print("题号有重复, 请检查.\n"*5)